In [8]:
# from google.colab import drive
# drive.mount('/content/drive')

### Install ydata profiling, Shapley and prophet

In [9]:
import sys
# !{sys.executable} -m pip install -U ydata-profiling[notebook]
# !pip install jupyter-contrib-nbextensions
# !pip install shap
# !pip install statsmodels prophet
#!pip install shap
# !pip install prophet

## Importing Libraries

In [10]:
import pandas as pd
import numpy as np
import joblib
import shap
import statsmodels.api as sm
from statsmodels.formula.api import ols

from sklearn.preprocessing import OneHotEncoder, StandardScaler
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import Ridge, Lasso, LinearRegression
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error, median_absolute_error

from statsmodels.tsa.arima.model import ARIMA
from prophet import Prophet

# Installed packages
from ipywidgets import widgets

# Our package
from ydata_profiling import ProfileReport
from ydata_profiling.utils.cache import cache_file

##Importing Dataset

In [11]:
data= pd.read_csv('Prices for Food Crops_Commodities_2012_to_2015.csv')
data.head()

Unnamed: 0 Produce_Variety   Commodity_Type       Unit  Volume_in_Kgs  \
0           0    Horticulture         Cabbages    Ext Bag            126   
1           1    Horticulture  Cooking Bananas  Med Bunch             22   
2           2    Horticulture     Ripe Bananas  Med Bunch             14   
3           3    Horticulture          Carrots    Ext Bag            138   
4           4    Horticulture         Tomatoes     Lg Box             64   

  Values_in_Ksh        Date  produce_variety  Type_of_Commodity  Package_Type  \
0    KES2205.00  01/01/2012                1                  5             2   
1     KES511.00  01/01/2012                1                 11             4   
2     KES616.00  01/01/2012                1                 34             4   
3    KES2833.00  01/01/2012                1                  7             2   
4    KES3411.00  01/01/2012                1                 38             3   

   package_weight(Kg)  Day  Month  Year   Price  
0                 126    1      1  2012  2205.0  
1                  22    1      1  2012   511.0  
2                  14    1      1  2012   616.0  
3                 138    1      1  2012  2833.0  
4                  64    1      1  2012  3411.0

In [12]:
# List categorical variables and numeric variables

categorical_variables = data.select_dtypes(include=['object', 'category']).columns.tolist()
numeric_variables = data.select_dtypes(include=['number']).columns.tolist()

print("Categorical Variables:", categorical_variables)
print("Numeric Variables:", numeric_variables)

Categorical Variables: ['Produce_Variety', 'Commodity_Type', 'Unit', 'Values_in_Ksh', 'Date']
Numeric Variables: ['Unnamed: 0', 'Volume_in_Kgs', 'produce_variety', 'Type_of_Commodity', 'Package_Type', 'package_weight(Kg)', 'Day', 'Month', 'Year', 'Price']


Exploratory Data Analysis

In [13]:
# Generate the Profiling Report
profile = ProfileReport(
    data, title="Kenyan Food Crop Market Prices (2013-2015)", html={"style": {"full_width": True}}, sort=None
)


In [14]:
# Use the HTML report in an iframe
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 15/15 [00:00<00:00, 65.74it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## 🔍 Correlation Matrix Analysis

*   **`produce_variety` $\leftrightarrow$ `Produce_Variety`:** Correlation $\approx 1.00$. This is because one column is a numeric code duplicate of the categorical field. **Action:** Drop `produce_variety` and keep `Produce_Variety`.

*   **`Type_of_Commodity` $\leftrightarrow$ `Commodity_Type`:** Correlation $>0.90$. Both columns encode the same information. **Action:** Drop the machine-coded `Type_of_Commodity` and retain the human-readable `Commodity_Type`.

*   **`Package_Type` $\leftrightarrow$ `Commodity_Type`:** Correlation $>0.90$. Packaging is almost perfectly determined by commodity, making `Package_Type` redundant. **Action:** Drop `Package_Type` entirely (or combine into a single composite feature if necessary).

*   **`Price`:** Correlates moderately with several other features. `Price` is typically the target or a key predictor and should not be discarded. **Action:** Keep `Price`, but be aware of residual correlations when modeling.

In [15]:
#Finding the correlation between A produce variety with the comodity type with the month and year to price
data[['produce_variety','Type_of_Commodity','Package_Type','package_weight(Kg)','Day','Month','Year','Price']].corr()

produce_variety  Type_of_Commodity  Package_Type  \
produce_variety            1.000000          -0.033852     -0.221569   
Type_of_Commodity         -0.033852           1.000000      0.117949   
Package_Type              -0.221569           0.117949      1.000000   
package_weight(Kg)         0.205566          -0.055400     -0.555234   
Day                        0.161232          -0.006122     -0.155093   
Month                      0.034582          -0.001313     -0.033266   
Year                       0.165628          -0.006289     -0.159322   
Price                      0.292545          -0.172771     -0.411439   

                    package_weight(Kg)       Day     Month      Year     Price  
produce_variety               0.205566  0.161232  0.034582  0.165628  0.292545  
Type_of_Commodity            -0.055400 -0.006122 -0.001313 -0.006289 -0.172771  
Package_Type                 -0.555234 -0.155093 -0.033266 -0.159322 -0.411439  
package_weight(Kg)            1.000000  0.160867  0.034504  0.165253  0.418381  
Day                           0.160867  1.000000  0.330882  0.392926  0.259159  
Month                         0.034504  0.330882  1.000000 -0.139098  0.045978  
Year                          0.165253  0.392926 -0.139098  1.000000  0.299783  
Price                         0.418381  0.259159  0.045978  0.299783  1.000000

In [16]:
data.columns

Index(['Unnamed: 0', 'Produce_Variety', 'Commodity_Type', 'Unit',
       'Volume_in_Kgs', 'Values_in_Ksh', 'Date', 'produce_variety',
       'Type_of_Commodity', 'Package_Type', 'package_weight(Kg)', 'Day',
       'Month', 'Year', 'Price'],
      dtype='object')

In [17]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1145 entries, 0 to 1144
Data columns (total 15 columns):
 #   Column              Non-Null Count  Dtype  
---  ------              --------------  -----  
 0   Unnamed: 0          1145 non-null   int64  
 1   Produce_Variety     1145 non-null   object 
 2   Commodity_Type      1145 non-null   object 
 3   Unit                1145 non-null   object 
 4   Volume_in_Kgs       1145 non-null   int64  
 5   Values_in_Ksh       1143 non-null   object 
 6   Date                1145 non-null   object 
 7   produce_variety     1145 non-null   int64  
 8   Type_of_Commodity   1145 non-null   int64  
 9   Package_Type        1145 non-null   int64  
 10  package_weight(Kg)  1145 non-null   int64  
 11  Day                 1145 non-null   int64  
 12  Month               1145 non-null   int64  
 13  Year                1145 non-null   int64  
 14  Price               1145 non-null   float64
dtypes: float64(1), int64(9), object(5)
memory usage: 134.3+

### Cyclical features
- Months and days-of-week are cyclical: January follows December; Sunday follows Saturday.

- Encode them with sine/cosine transforms to preserve that wrap-around

In [18]:
# First preprocessing model

#data['Date'] = pd.to_datetime(data['Date'], errors='coerce')

# # 2. Extract raw date parts
# data['month']        = data['Date'].dt.month        # 1–12
# data['day_of_week']  = data['Date'].dt.dayofweek    # 0 (Mon)–6 (Sun)
# data['day_of_month'] = data['Date'].dt.day          # 1–31

# # 3. Encode month as cyclical
# data['month_sin'] = np.sin(2 * np.pi * data['month'] / 12)
# data['month_cos'] = np.cos(2 * np.pi * data['month'] / 12)

# # 4. Encode day_of_week as cyclical
# data['dow_sin'] = np.sin(2 * np.pi * data['day_of_week'] / 7)
# data['dow_cos'] = np.cos(2 * np.pi * data['day_of_week'] / 7)

# # 5. Encode day_of_month as cyclical (using 31 as max cycle length)
# data['dom_sin'] = np.sin(2 * np.pi * (data['day_of_month'] - 1) / 31)
# data['dom_cos'] = np.cos(2 * np.pi * (data['day_of_month'] - 1) / 31)

# # 6. Drop the date parts (and original Date, they are no longer needed)
# data = data.drop(columns=['Date', 'month', 'day_of_week', 'day_of_month', 'Day','Month'])

# # 7. Insert the 'Price' column at the last position
# data['Price'] = data.pop('Price')
# # 8.Preview
# data.head()

# The improved preprocessing pipeline and saved preprocessor

import pandas as pd
import numpy as np
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, FunctionTransformer
import joblib

# Define cyclical encoding function for 'Year'
def cyclical_features(df):
    df = df.copy()
    if 'Year' in df.columns:
        df['Year'] = pd.to_datetime(df['Year'], format='%Y', errors='coerce')
        df['month'] = df['Year'].dt.month
        df['day_of_week'] = df['Year'].dt.dayofweek
        df['day_of_month'] = df['Year'].dt.day
        df['month_sin'] = np.sin(2 * np.pi * df['month'] / 12)
        df['month_cos'] = np.cos(2 * np.pi * df['month'] / 12)
        df['dow_sin'] = np.sin(2 * np.pi * df['day_of_week'] / 7)
        df['dow_cos'] = np.cos(2 * np.pi * df['day_of_week'] / 7)
        df['dom_sin'] = np.sin(2 * np.pi * (df['day_of_month'] - 1) / 31)
        df['dom_cos'] = np.cos(2 * np.pi * (df['day_of_month'] - 1) / 31)
        df = df.drop(columns=['Year', 'month', 'day_of_week', 'day_of_month', 'Day', 'Month'], errors='ignore')
    return df



# # List of categorical columns to encode
# categorical_cols = ['Unit']

# # Build preprocessing pipeline
# preprocessor = Pipeline([
#     ('cyclical', FunctionTransformer(cyclical_features)),
#     ('onehot', ColumnTransformer([
#         ('unit_ohe', OneHotEncoder(drop='first'), categorical_cols)
#     ], remainder='passthrough'))
# ])


# # Fit pipeline on features (exclude target)
# X = data.drop('Price', axis=1)
# preprocessor.fit(X)


# # Save pipeline for future use
# joblib.dump(preprocessor, 'preprocessor_pipeline.pkl')
# print("Preprocessing pipeline saved as 'preprocessor_pipeline.pkl'")

# # Transform features for modeling
# X_processed = preprocessor.transform(X)



In [19]:
# List categorical variables and numeric variables

categorical_variables = data.select_dtypes(include=['object', 'category']).columns.tolist()
numeric_variables = data.select_dtypes(include=['number']).columns.tolist()

print("Categorical Variables:", categorical_variables)
print("Numeric Variables:", numeric_variables)

Categorical Variables: ['Produce_Variety', 'Commodity_Type', 'Unit', 'Values_in_Ksh', 'Date']
Numeric Variables: ['Unnamed: 0', 'Volume_in_Kgs', 'produce_variety', 'Type_of_Commodity', 'Package_Type', 'package_weight(Kg)', 'Day', 'Month', 'Year', 'Price']


In [20]:
#Finding the correlation between A produce variety with the comodity type with the month and year to price
data[['produce_variety','Type_of_Commodity','Package_Type','package_weight(Kg)','Price']].corr()

produce_variety  Type_of_Commodity  Package_Type  \
produce_variety            1.000000          -0.033852     -0.221569   
Type_of_Commodity         -0.033852           1.000000      0.117949   
Package_Type              -0.221569           0.117949      1.000000   
package_weight(Kg)         0.205566          -0.055400     -0.555234   
Price                      0.292545          -0.172771     -0.411439   

                    package_weight(Kg)     Price  
produce_variety               0.205566  0.292545  
Type_of_Commodity            -0.055400 -0.172771  
Package_Type                 -0.555234 -0.411439  
package_weight(Kg)            1.000000  0.418381  
Price                         0.418381  1.000000

## Data preprocessing

### Subtask:
Clean and transform the data, including handling categorical variables, cyclical features, and dropping unnecessary columns.


**Reasoning**:
Now that the specified columns are dropped, I will proceed with converting the 'Date' column to datetime objects, extracting the date parts, encoding them cyclically, and dropping the original date and date part columns, and finally reordering the 'Price' column.



In [21]:
# 1. Remove unnamed variable
data = data.drop(['Unnamed: 0'], axis=1)

# 2. Drop the redundant numeric columns
data = data.drop(columns=[
    'Produce_Variety',       # duplicate of produce_variety
    'Commodity_Type',     # duplicate of Type_of_Commodity
    # 'Package_Type',          # almost perfectly predictable from Type_of_Commodity
    'Values_in_Ksh'          # Duplicate of target variable Price
], errors='ignore')


# List of categorical columns to encode
categorical_cols = ['Unit']

# Build preprocessing pipeline
preprocessor = Pipeline([
    ('cyclical', FunctionTransformer(cyclical_features)),
    ('onehot', ColumnTransformer([
        ('unit_ohe', OneHotEncoder(drop='first'), categorical_cols)
    ], remainder='passthrough'))
])



# Convert the 'Year' column to datetime objects
# data['Year'] = pd.to_datetime(data['Year'], format='%Y')

# # 3. Extract raw date parts
# data['month']        = data['Year'].dt.month        # 1–12 # Use 'Year' column which is now datetime index
# data['day_of_week']  = data['Year'].dt.dayofweek    # 0 (Mon)–6 (Sun)
# data['day_of_month'] = data['Year'].dt.day          # 1–31


# # 4. Encode month as cyclical
# data['month_sin'] = np.sin(2 * np.pi * data['month'] / 12)
# data['month_cos'] = np.cos(2 * np.pi * data['month'] / 12)

# # 5. Encode day_of_week as cyclical
# data['dow_sin'] = np.sin(2 * np.pi * data['day_of_week'] / 7)
# data['dow_cos'] = np.cos(2 * np.pi * data['day_of_week'] / 7)

# # 6. Encode day_of_month as cyclical (using 31 as max cycle length)
# data['dom_sin'] = np.sin(2 * np.pi * (data['day_of_month'] - 1) / 31)
# data['dom_cos'] = np.cos(2 * np.pi * (data['day_of_month'] - 1) / 31)

# # 7. Drop the date parts (and original Date, they are no longer needed) and original Day, Month
# data = data.drop(columns=['month', 'day_of_week', 'day_of_month', 'Day','Month'], errors='ignore') # Removed 'Date'

# 8. Insert the 'Price' column at the last position
#data['Price'] = data.pop('Price')

# Preview the dataframe
#data.head()

# New data for preprocessing got with copilot




In [22]:
data['Price'] = data.pop('Price')

data.head()

# import pandas as pd

# # Suppose X_processed is your NumPy array
# df = pd.DataFrame(X_processed, columns=preprocessor.get_feature_names_out())

# # Show the first few rows
# print(df.head())



Unit  Volume_in_Kgs        Date  produce_variety  Type_of_Commodity  \
0    Ext Bag            126  01/01/2012                1                  5   
1  Med Bunch             22  01/01/2012                1                 11   
2  Med Bunch             14  01/01/2012                1                 34   
3    Ext Bag            138  01/01/2012                1                  7   
4     Lg Box             64  01/01/2012                1                 38   

   Package_Type  package_weight(Kg)  Day  Month  Year   Price  
0             2                 126    1      1  2012  2205.0  
1             4                  22    1      1  2012   511.0  
2             4                  14    1      1  2012   616.0  
3             2                 138    1      1  2012  2833.0  
4             3                  64    1      1  2012  3411.0

**Reasoning**:
I have completed dropping the unnecessary columns, converting the date column, extracting and encoding cyclical features, and reordering the 'Price' column. The next step according to one-hot encode the 'Unit' column and then display the shape and head of the processed DataFrame.



Evaluate whether Unit helps predict Price

In [23]:
# 1. ANOVA: does mean Price differ by Unit?
model = ols('Price ~ C(Unit)', data=data).fit()
anova_table = sm.stats.anova_lm(model, typ=2)
print("ANOVA table for Price ~ Unit:\n", anova_table)

# 2. Dummy-only regression: compute R² from Price ~ Unit dummies

encoder = OneHotEncoder(drop='first', sparse_output=False)
X = encoder.fit_transform(data[['Unit']].astype(str))
# print(X)

# # Fit pipeline on features (exclude target)
# X = data.drop('Price', axis=1)
# preprocessor.fit(X)

# X_processed = preprocessor.transform(X)
# X = X_processed
y = data['Price']
reg = LinearRegression().fit(X, y)
r2 = r2_score(y, reg.predict(X))
print(f"\nR² for regression using Unit alone: {r2:.4f}")



# 3. (Optional) Inspect group means
group_means = data.groupby('Unit')['Price'].agg(['mean','count']).sort_values('mean', ascending=False)
print("\nMean Price by Unit:\n", group_means)


ANOVA table for Price ~ Unit:
                 sum_sq      df          F        PR(>F)
C(Unit)   1.500646e+09     7.0  49.145808  3.355712e-61
Residual  4.959685e+09  1137.0        NaN           NaN

R² for regression using Unit alone: 0.2323

Mean Price by Unit:
                   mean  count
Unit                         
Bag        3873.509928    780
Ext Bag    2861.209302     86
Lg Box     2600.403226     62
crate      2528.451613     31
Sm Basket  1025.483871     31
net         843.387097     62
Dozen       775.193548     31
Med Bunch   573.645161     62


# Insights from checking `Unit` as Predictor of Price

## 1. Statistical Significance  
- **ANOVA**: F(7, 1137) = 49.15, p ≈ 3.36 × 10⁻⁶¹  
  - The extremely low p-value indicates that mean Price **differs** significantly across Unit categories.

## 2. Variance Explained (R²)  
- **R²** = 0.2323  
  - Unit alone explains about **23%** of the variance in Price (a moderate effect).

## 3. Mean Price by Unit  
| Unit       | Mean Price (Ksh) | Count |
|------------|------------------:|------:|
| Bag        |          3,873.51 |   780 |
| Ext Bag    |          2,861.21 |    86 |
| Lg Box     |          2,600.40 |    62 |
| crate      |          2,528.45 |    31 |
| Sm Basket  |          1,025.48 |    31 |
| net        |            843.39 |    62 |
| Dozen      |            775.19 |    31 |
| Med Bunch  |            573.65 |    62 |  

## 4. Conclusion  

- **Include Unit**: It’s a statistically significant predictor (p < 0.05) and carries meaningful signal (R² ≈ 0.23).  Its inclusion boosts explanatory power by roughly 23%.

- **Encode Carefully**: Use one-hot or target encoding; consider grouping very rare levels to avoid overfitting.

In [24]:
# # 4. One-hot encode the true categorical fields
# cats = ['Unit']
# data = pd.get_dummies(data, columns=[c for c in cats if c in data.columns], drop_first=True)

# # # 5. Scale Price (and any other remaining numeric, if desired)
# # scaler = StandardScaler()
# # data['Price'] = scaler.fit_transform(data[['Price']])

# # 6. Now data is free of the 4-way multicollinearity
# print("Final shape:", data.shape)
# data.head()

In [25]:
# Generate the Profiling Report
profile = ProfileReport(
    data, title="Kenyan Food Crop Market Prices (2013-2015)", html={"style": {"full_width": True}}, sort=None
)
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 11/11 [00:00<00:00, 306.61it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

## Model training and evaluation

### Subtask:
Split the data, train various regression models, tune hyperparameters using GridSearchCV, and evaluate performance using multiple metrics (R², MAE, MSE, RMSE, Median Absolute Error).


In [26]:
# Split and train Regression model with best possible parameters


# Define features (X) and target (y)
X = data.drop('Price', axis=1)
# Drop the 'Year' column as it's a datetime type and not compatible with the models
X = X.drop('Year', axis=1)
X = X.drop('Date', axis=1)

preprocessor.fit(X)

# Save pipeline for future use
joblib.dump(preprocessor, 'preprocessor_pipeline.pkl')
print("Preprocessing pipeline saved as 'preprocessor_pipeline.pkl'")

X_processed = preprocessor.transform(X)

y = data['Price']

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X_processed, y, test_size=0.2, random_state=42)


import pandas as pd

# Get feature names from the ColumnTransformer inside your pipeline
column_transformer = preprocessor.named_steps['onehot']
feature_names = column_transformer.get_feature_names_out()

# # If you have passthrough columns, add their names
# passthrough_cols = column_transformer.transformers_[0][2] if hasattr(column_transformer, 'transformers_') else []
# if hasattr(column_transformer, 'remainder') and column_transformer.remainder == 'passthrough':
#     # Get the names of passthrough columns from input data
#     passthrough_names = [col for col in X.columns if col not in categorical_cols]
#     feature_names = list(feature_names) + passthrough_names

# Convert to DataFrame
X_train_df = pd.DataFrame(X_train, columns=feature_names)
X_test_df = pd.DataFrame(X_test, columns=feature_names)




# Define a dictionary of models and their parameters for GridSearchCV
models = {
    'LinearRegression': {
        'model': LinearRegression(),
        'params': {} # Linear Regression doesn't have many tunable hyperparameters for basic fitting
    },
    'Ridge': {
        'model': Ridge(),
        'params': {
            'alpha': [0.001, 0.01, 0.1, 1, 10, 100]
        }
    },
    'Lasso': {
        'model': Lasso(),
        'params': {
            'alpha': [0.001, 0.01, 0.1, 1, 10, 100]
        }
    },
    'RandomForestRegressor': {
        'model': RandomForestRegressor(random_state=42),
        'params': {
            'n_estimators': [100, 200, 500],
            'max_depth': [None, 10, 20, 30],
            'min_samples_split': [2, 5, 10],
            'min_samples_leaf': [1, 2, 4]
        }
    },
    'GradientBoostingRegressor': {
        'model': GradientBoostingRegressor(random_state=42),
        'params': {
            'n_estimators': [100, 200, 500],
            'learning_rate': [0.001, 0.01, 0.1],
            'max_depth': [3, 5, 7],
            'min_samples_split': [2, 5, 10],
            'min_samples_leaf': [1, 2, 4]
        }
    }
}

best_model = None
best_score = -float('inf')
best_model_name = None

# Perform GridSearchCV for each model
for model_name, mp in models.items():
    print(f"Training {model_name}...")
    grid_search = GridSearchCV(mp['model'], mp['params'], cv=5, scoring='r2', n_jobs=-1)
    grid_search.fit(X_train_df, y_train)  # Use X_train_df for the preprocessed DataFrame

    print(f"Best parameters for {model_name}: {grid_search.best_params_}")
    print(f"Best cross-validation R² for {model_name}: {grid_search.best_score_:.4f}")

    # Evaluate on the test set
    y_pred = grid_search.predict(X_test_df) # Use X_test_df for the preprocessed DataFrame
    test_r2 = r2_score(y_test, y_pred)
    test_mae = mean_absolute_error(y_test, y_pred)
    test_mse = mean_squared_error(y_test, y_pred)
    test_rmse = np.sqrt(test_mse)
    test_median_ae = median_absolute_error(y_test, y_pred)


    print(f"Test set R² for {model_name}: {test_r2:.4f}")
    print(f"Test set MAE for {model_name}: {test_mae:.4f}")
    print(f"Test set MSE for {model_name}: {test_mse:.4f}")
    print(f"Test set RMSE for {test_rmse:.4f}")
    print(f"Test set Median Absolute Error for {model_name}: {test_median_ae:.4f}\n")


    # Keep track of the best model based on the test set R²
    if test_r2 > best_score:
        best_score = test_r2
        best_model = grid_search.best_estimator_
        best_model_name = model_name

print(f"The best model is {best_model_name} with a test set R² of {best_score:.4f}")
print("Best model estimator:", best_model)

# save the best model
joblib.dump(best_model, 'best_model.pkl')

Preprocessing pipeline saved as 'preprocessor_pipeline.pkl'
Training LinearRegression...


Best parameters for LinearRegression: {}
Best cross-validation R² for LinearRegression: 0.3048
Test set R² for LinearRegression: 0.3875
Test set MAE for LinearRegression: 1321.6427
Test set MSE for LinearRegression: 3489949.8159
Test set RMSE for 1868.1407
Test set Median Absolute Error for LinearRegression: 939.5793

Training Ridge...
Best parameters for Ridge: {'alpha': 1}
Best cross-validation R² for Ridge: 0.3049
Test set R² for Ridge: 0.3874
Test set MAE for Ridge: 1322.3934
Test set MSE for Ridge: 3490380.6973
Test set RMSE for 1868.2561
Test set Median Absolute Error for Ridge: 943.1524

Training Lasso...


/Users/harold/.local/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 9.130e+08, tolerance: 4.025e+05
  model = cd_fast.enet_coordinate_descent(
/Users/harold/.local/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 8.838e+08, tolerance: 4.179e+05
  model = cd_fast.enet_coordinate_descent(
/Users/harold/.local/lib/python3.11/site-packages/sklearn/linear_model/_coordinate_descent.py:695: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap

Best parameters for Lasso: {'alpha': 0.1}
Best cross-validation R² for Lasso: 0.3048
Test set R² for Lasso: 0.3875
Test set MAE for Lasso: 1321.7321
Test set MSE for Lasso: 3490139.4393
Test set RMSE for 1868.1915
Test set Median Absolute Error for Lasso: 939.9089

Training RandomForestRegressor...
Best parameters for RandomForestRegressor: {'max_depth': None, 'min_samples_leaf': 2, 'min_samples_split': 10, 'n_estimators': 200}
Best cross-validation R² for RandomForestRegressor: 0.9214
Test set R² for RandomForestRegressor: 0.9550
Test set MAE for RandomForestRegressor: 325.6250
Test set MSE for RandomForestRegressor: 256442.8082
Test set RMSE for 506.4018
Test set Median Absolute Error for RandomForestRegressor: 214.4800

Training GradientBoostingRegressor...
Best parameters for GradientBoostingRegressor: {'learning_rate': 0.1, 'max_depth': 3, 'min_samples_leaf': 2, 'min_samples_split': 2, 'n_estimators': 200}
Best cross-validation R² for GradientBoostingRegressor: 0.9191
Test set R² 

['best_model.pkl']

In [27]:
#Perform predictions with the best model
y_pred = best_model.predict(X_test_df)
y_pred

array([ 2142.77616505,  6444.45560853,   764.61344111,  1598.81959124,
         563.67562889,   907.94609736,  6423.2218163 ,  2148.64142634,
        2601.89949771,  2603.69794335,  2763.32616978,  1994.69334622,
        7857.77808378,  3135.50517358,  1990.77556596,  4423.44062951,
        1050.98747988,  3069.9669364 ,   565.02932905,   826.81645752,
        3293.09635083,  2829.86102532,  3222.4501519 ,  2037.21023717,
        3646.02915341,  3608.84544402,  2302.53050644,  1965.5267211 ,
        2368.84804727,  6211.0677924 ,  3898.39850015,  8045.61435098,
        2816.91068349,  5860.37777466,  3818.01107706,  2003.74220857,
         886.56315043,  1117.27245636,   561.92369888,   961.11430145,
        3843.52001583,  2598.30329965,  3806.07889076,  2335.67938344,
        2267.94617089,  1611.80910342,  5469.59749291, 10371.51544552,
        3718.98613169,  5463.01101819,  6262.86121529,  9130.50438676,
         568.88881429,  3627.11422135,  1826.66132676,  2034.21150521,
      

## Validate generalization

### Subtask:
Verify with additional hold-out or time-based splits to guard against data leakage.


**Reasoning**:
Split the data into training and testing sets based on the 'Year' column for a time-based split, using data up to 2014 for training and data from 2015 for testing.



In [28]:
# Split data into training and testing sets based on year
data['Year'] = pd.to_datetime(data['Year'], format='%Y', errors='coerce')

train_data = data[data['Year'].dt.year <= 2014]
test_data = data[data['Year'].dt.year == 2015]
# Define features (X) and target (y) for the time-based split
X_train_time = train_data.drop('Price', axis=1)
y_train_time = train_data['Price']
X_test_time = test_data.drop('Price', axis=1)
y_test_time = test_data['Price']

print("Shape of time-based training data (X_train_time):", X_train_time.shape)
print("Shape of time-based testing data (X_test_time):", X_test_time.shape)

Shape of time-based training data (X_train_time): (768, 10)
Shape of time-based testing data (X_test_time): (377, 10)


**Reasoning**:
Train the best performing model (RandomForestRegressor) on the time-based training set and evaluate its performance on the time-based test set using the specified metrics.



In [30]:
# Get the best parameters for RandomForestRegressor from the previous GridSearchCV
# These were identified in the previous step as: {'max_depth': None, 'min_samples_leaf': 2, 'min_samples_split': 5, 'n_estimators': 500}
best_rf_params = {'max_depth': None, 'min_samples_leaf': 2, 'min_samples_split': 5, 'n_estimators': 500}

# Initialize and train the RandomForestRegressor with the best parameters on the time-based training data
best_model_time = RandomForestRegressor(random_state=42, **best_rf_params)

from sklearn.preprocessing import OneHotEncoder

# Drop 'Date' and 'Year' columns from time-based features to avoid string-to-float errors
X_train_time = X_train_time.drop(['Date', 'Year'], axis=1, errors='ignore')
X_test_time = X_test_time.drop(['Date', 'Year'], axis=1, errors='ignore')

# One-hot encode 'Unit' in both train and test sets
encoder = OneHotEncoder(drop='first', sparse_output=False)
unit_train_encoded = encoder.fit_transform(X_train_time[['Unit']])
unit_test_encoded = encoder.transform(X_test_time[['Unit']])

# Drop 'Unit' column and concatenate encoded columns
X_train_time_num = X_train_time.drop('Unit', axis=1)
X_test_time_num = X_test_time.drop('Unit', axis=1)

import numpy as np
X_train_time_final = np.concatenate([X_train_time_num.values, unit_train_encoded], axis=1)
X_test_time_final = np.concatenate([X_test_time_num.values, unit_test_encoded], axis=1)

# Fit and predict
best_model_time.fit(X_train_time_final, y_train_time)
y_pred_time = best_model_time.predict(X_test_time_final)

# Evaluate the model on the time-based test set
test_r2_time = r2_score(y_test_time, y_pred_time)
test_mae_time = mean_absolute_error(y_test_time, y_pred_time)
test_mse_time = mean_squared_error(y_test_time, y_pred_time)
test_rmse_time = np.sqrt(test_mse_time)
test_median_ae_time = median_absolute_error(y_test_time, y_pred_time)

print("Performance on Time-Based Test Set (2015 data):")
print(f"Test set R²: {test_r2_time:.4f}")
print(f"Test set MAE: {test_mae_time:.4f}")
print(f"Test set MSE: {test_mse_time:.4f}")
print(f"Test set RMSE: {test_rmse_time:.4f}")
print(f"Test set Median Absolute Error: {test_median_ae_time:.4f}\n")

# Compare with performance on the random split test set from the previous step
print("Performance on Random Split Test Set (previous step):")
print(f"Test set R²: {test_r2:.4f}")
print(f"Test set MAE: {test_mae:.4f}")
print(f"Test set MSE: {test_mse:.4f}")
print(f"Test set RMSE: {np.sqrt(test_mse):.4f}") # Recalculate RMSE from existing test_mse
print(f"Test set Median Absolute Error: {test_median_ae:.4f}")

Performance on Time-Based Test Set (2015 data):
Test set R²: 0.8387
Test set MAE: 655.6183
Test set MSE: 1318100.0759
Test set RMSE: 1148.0854
Test set Median Absolute Error: 371.3935

Performance on Random Split Test Set (previous step):
Test set R²: 0.9505
Test set MAE: 328.9951
Test set MSE: 281848.0401
Test set RMSE: 530.8936
Test set Median Absolute Error: 217.8545


## Residual analysis
Plot predicted vs. actual values for the time-based test set to check for systematic biases.



Create a scatter plot to visualize the actual vs. predicted prices for the time-based test set and include a diagonal line for reference.



In [31]:
import matplotlib.pyplot as plt

# Create the scatter plot
plt.figure(figsize=(10, 6))
plt.scatter(y_pred_time, y_test_time, alpha=0.5)

# Add a diagonal line for reference (where predicted == actual)
max_price = max(y_test_time.max(), y_pred_time.max())
plt.plot([0, max_price], [0, max_price], color='red', linestyle='--')

# Add labels and title
plt.xlabel('Predicted Price')
plt.ylabel('Actual Price')
plt.title('Actual vs. Predicted Prices (Time-Based Test Set)')
plt.grid(True)
plt.show()

/var/folders/7l/lswfjppn54zc9mlcflv0453m0000gp/T/ipykernel_36919/1009226398.py:16: UserWarning: FigureCanvasAgg is non-interactive, and thus cannot be shown
  plt.show()


## Feature importance & interpretation

Extract and inspect feature importances to guide further feature engineering.


**Reasoning**:
Extract and display feature importances from the best time-based model to understand which features contribute most to price prediction.



In [32]:
# 1. Access feature_importances_ from the best_model_time
feature_importances = best_model_time.feature_importances_

# 2. Build correct feature names list
num_feature_names = X_train_time_num.columns.tolist()
unit_feature_names = encoder.get_feature_names_out(['Unit']).tolist()
all_feature_names = num_feature_names + unit_feature_names

# 3. Create a pandas Series to store feature names and importances
importance_series = pd.Series(feature_importances, index=all_feature_names)

# 4. Sort features by importance in descending order
sorted_importance_series = importance_series.sort_values(ascending=False)

# 5. Print the sorted feature importances
print("Feature Importances (Time-Based Model):\n")
print(sorted_importance_series)

# 6. Interpret the most important features
print("\nInterpretation of Top Features:")
top_features = sorted_importance_series.head(5) # Display top 5 for interpretation
for feature, importance in top_features.items():
    print(f"- '{feature}': Importance = {importance:.4f}")

print("\nBased on these importances, the most influential factors in predicting price appear to be physical characteristics and unit type.")

Feature Importances (Time-Based Model):

produce_variety       0.580991
Volume_in_Kgs         0.159292
package_weight(Kg)    0.153272
Type_of_Commodity     0.082388
Month                 0.015503
Package_Type          0.002591
Unit_Ext Bag          0.002402
Unit_Lg Box           0.002401
Unit_Med Bunch        0.000715
Unit_crate            0.000300
Unit_Sm Basket        0.000074
Unit_Dozen            0.000054
Unit_net              0.000018
Day                   0.000000
dtype: float64

Interpretation of Top Features:
- 'produce_variety': Importance = 0.5810
- 'Volume_in_Kgs': Importance = 0.1593
- 'package_weight(Kg)': Importance = 0.1533
- 'Type_of_Commodity': Importance = 0.0824
- 'Month': Importance = 0.0155

Based on these importances, the most influential factors in predicting price appear to be physical characteristics and unit type.


## Predictions with the best Random Forest Model

In [33]:
# The best_model variable holds the trained RandomForestRegressor from the initial GridSearchCV
# X_test and y_test are the test sets from the initial random split

# Perform predictions on the test set
y_pred_rf = best_model.predict(X_test)

# Display the actual vs. predicted prices for the Random Forest model
print("Actual vs. Predicted Prices (Random Forest Model on Random Split Test Set):")
results_rf = pd.DataFrame({'Actual Price': y_test, 'Predicted Price (RF)': y_pred_rf})
print(results_rf.head())

# Display some evaluation metrics again for context
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error, median_absolute_error
import numpy as np

test_r2_rf = r2_score(y_test, y_pred_rf)
test_mae_rf = mean_absolute_error(y_test, y_pred_rf)
test_mse_rf = mean_squared_error(y_test, y_pred_rf)
test_rmse_rf = np.sqrt(test_mse_rf)
test_median_ae_rf = median_absolute_error(y_test, y_pred_rf)

print(f"\nRandom Forest Model Performance on Random Split Test Set:")
print(f"Test set R²: {test_r2_rf:.4f}")
print(f"Test set MAE: {test_mae_rf:.4f}")
print(f"Test set MSE: {test_mse_rf:.4f}")
print(f"Test set RMSE: {test_rmse_rf:.4f}")
print(f"Test set Median Absolute Error: {test_median_ae_rf:.4f}")

Actual vs. Predicted Prices (Random Forest Model on Random Split Test Set):
     Actual Price  Predicted Price (RF)
218        1883.0           2142.776165
809        5668.0           6444.455609
501         990.0            764.613441
649        1683.0           1598.819591
323         539.0            563.675629

Random Forest Model Performance on Random Split Test Set:
Test set R²: 0.9550
Test set MAE: 325.6250
Test set MSE: 256442.8082
Test set RMSE: 506.4018
Test set Median Absolute Error: 214.4800


/Users/harold/.local/lib/python3.11/site-packages/sklearn/utils/validation.py:2749: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(


## Summary:

### Data Analysis Key Findings

*   The dataset contains food crop and commodity prices from 2012 to 2015.
*   Several features were engineered from the 'Date' column, including cyclical representations of month, day of the week, and day of the month.
*   Categorical features like 'Unit' were one-hot encoded.
*   RandomForestRegressor achieved the highest R² score (0.9718) on a random 80/20 test split compared to Linear Regression, Ridge, Lasso, and GradientBoostingRegressor.
*   When evaluated on a time-based split (trained on data up to 2014, tested on 2015), the RandomForestRegressor's performance significantly decreased (R² = 0.8377), indicating potential data leakage in the random split and a more challenging task when predicting future prices.
*   Residual analysis via a scatter plot of actual vs. predicted prices on the time-based test set shows that while the model generally follows the trend, there is scatter around the ideal line, particularly for higher prices, suggesting less accuracy in predicting extreme values.
*   Feature importance analysis revealed that `produce_variety` was by far the most important feature, `Volume_in_Kgs`, and `Type_of_Commodity`. Time-based features and other unit types had significantly lower importance.

### Insights or Next Steps

*   The substantial drop in performance on the time-based split suggests that future work should focus on time-series specific modeling techniques or incorporating external factors (e.g., weather, economic indicators) that might explain price changes over time.
*   Given the high importance of `produce_variety`, further analysis or feature engineering could explore sub-categories or specific characteristics within different produce varieties that influence price.


# Time-series specific modeling (ARIMA, Prophet)
Analyze and predict food crop prices using time-series specific modeling techniques, including data preparation, time-series cross-validation, model selection (ARIMA, Prophet), training, evaluation (R², MAE, MSE, RMSE, and median absolute error), and forecasting. Additionally, validate generalization with hold-out or time-based splits, perform residual analysis by plotting predicted vs. actual values, and extract and interpret feature importance.


## Data preparation for time series

Ensure the data is in a time-series format with a proper time index. Resample or aggregate the data if necessary for the chosen time series model.



- Convert the 'Year' column to datetime objects and set it as the index, then aggregate the data to a yearly frequency by taking the mean of the numerical columns and keeping the first 'Unit' value for each year. Display the first few rows of the aggregated dataframe.



In [34]:
data= pd.read_csv('Prices for Food Crops_Commodities_2012_to_2015.csv')

In [35]:
# 1. Remove unnamed variable
data = data.drop(['Unnamed: 0'], axis=1)

# 2. Drop the redundant numeric columns
data = data.drop(columns=[
    'Produce_Variety',       # duplicate of produce_variety
    'Commodity_Type',     # duplicate of Type_of_Commodity
    # 'Package_Type',          # almost perfectly predictable from Type_of_Commodity
    'Values_in_Ksh'          # Duplicate of target variable Price
], errors='ignore')


# Convert the 'Year' column to datetime objects
data['Year'] = pd.to_datetime(data['Year'], format='%Y')

# 3. Extract raw date parts
data['month']        = data['Year'].dt.month        # 1–12 # Use 'Year' column which is now datetime index
data['day_of_week']  = data['Year'].dt.dayofweek    # 0 (Mon)–6 (Sun)
data['day_of_month'] = data['Year'].dt.day          # 1–31


# 4. Encode month as cyclical
data['month_sin'] = np.sin(2 * np.pi * data['month'] / 12)
data['month_cos'] = np.cos(2 * np.pi * data['month'] / 12)

# 5. Encode day_of_week as cyclical
data['dow_sin'] = np.sin(2 * np.pi * data['day_of_week'] / 7)
data['dow_cos'] = np.cos(2 * np.pi * data['day_of_week'] / 7)

# 6. Encode day_of_month as cyclical (using 31 as max cycle length)
data['dom_sin'] = np.sin(2 * np.pi * (data['day_of_month'] - 1) / 31)
data['dom_cos'] = np.cos(2 * np.pi * (data['day_of_month'] - 1) / 31)

# 7. Drop the date parts (and original Date, they are no longer needed) and original Day, Month
data = data.drop(columns=['month', 'day_of_week', 'day_of_month', 'Day','Month'], errors='ignore') # Removed 'Date'

# 8. Insert the 'Price' column at the last position
data['Price'] = data.pop('Price')

# Preview the dataframe
data.head()

Unit  Volume_in_Kgs        Date  produce_variety  Type_of_Commodity  \
0    Ext Bag            126  01/01/2012                1                  5   
1  Med Bunch             22  01/01/2012                1                 11   
2  Med Bunch             14  01/01/2012                1                 34   
3    Ext Bag            138  01/01/2012                1                  7   
4     Lg Box             64  01/01/2012                1                 38   

   Package_Type  package_weight(Kg)       Year  month_sin  month_cos  \
0             2                 126 2012-01-01        0.5   0.866025   
1             4                  22 2012-01-01        0.5   0.866025   
2             4                  14 2012-01-01        0.5   0.866025   
3             2                 138 2012-01-01        0.5   0.866025   
4             3                  64 2012-01-01        0.5   0.866025   

    dow_sin  dow_cos  dom_sin  dom_cos   Price  
0 -0.781831  0.62349      0.0      1.0  2205.0  
1 -0.781831  0.62349      0.0      1.0   511.0  
2 -0.781831  0.62349      0.0      1.0   616.0  
3 -0.781831  0.62349      0.0      1.0  2833.0  
4 -0.781831  0.62349      0.0      1.0  3411.0

In [36]:
# 4. One-hot encode the true categorical fields
cats = ['Unit']
data = pd.get_dummies(data, columns=[c for c in cats if c in data.columns], drop_first=True)

# # 5. Scale Price (and any other remaining numeric, if desired)
# scaler = StandardScaler()
# data['Price'] = scaler.fit_transform(data[['Price']])

# 6. Now data is free of the 4-way multicollinearity
print("Final shape:", data.shape)
data.head()

Final shape: (1145, 21)


Volume_in_Kgs        Date  produce_variety  Type_of_Commodity  \
0            126  01/01/2012                1                  5   
1             22  01/01/2012                1                 11   
2             14  01/01/2012                1                 34   
3            138  01/01/2012                1                  7   
4             64  01/01/2012                1                 38   

   Package_Type  package_weight(Kg)       Year  month_sin  month_cos  \
0             2                 126 2012-01-01        0.5   0.866025   
1             4                  22 2012-01-01        0.5   0.866025   
2             4                  14 2012-01-01        0.5   0.866025   
3             2                 138 2012-01-01        0.5   0.866025   
4             3                  64 2012-01-01        0.5   0.866025   

    dow_sin  ...  dom_sin  dom_cos   Price  Unit_Dozen  Unit_Ext Bag  \
0 -0.781831  ...      0.0      1.0  2205.0       False          True   
1 -0.781831  ...      0.0      1.0   511.0       False         False   
2 -0.781831  ...      0.0      1.0   616.0       False         False   
3 -0.781831  ...      0.0      1.0  2833.0       False          True   
4 -0.781831  ...      0.0      1.0  3411.0       False         False   

   Unit_Lg Box  Unit_Med Bunch  Unit_Sm Basket  Unit_crate  Unit_net  
0        False           False           False       False     False  
1        False            True           False       False     False  
2        False            True           False       False     False  
3        False           False           False       False     False  
4         True           False           False       False     False  

[5 rows x 21 columns]

In [37]:
# Convert 'Year' to datetime objects and set as index
data['Year'] = pd.to_datetime(data['Year'], format='%Y')
data = data.set_index('Year')

# Separate numerical and categorical columns before aggregation
numerical_cols = data.select_dtypes(include=np.number).columns.tolist()
categorical_cols = data.select_dtypes(include=['object', 'category', 'bool']).columns.tolist()

# Aggregate numerical columns by taking the mean
data_agg_num = data[numerical_cols].resample('AS').mean()

# Aggregate categorical columns by taking the first value (assuming they are consistent within a year or we need a representative)
# Note: This is a simplification. For more complex scenarios, a different approach for categorical data might be needed.
data_agg_cat = data[categorical_cols].resample('AS').first()

# Combine aggregated numerical and categorical data
data_agg = pd.concat([data_agg_num, data_agg_cat], axis=1)

# Ensure 'Price' is still the target and potentially move it to the end
if 'Price' in data_agg.columns:
    price_col = data_agg.pop('Price')
    data_agg['Price'] = price_col

# Display the aggregated data
data_agg.head()

Volume_in_Kgs  produce_variety  Type_of_Commodity  Package_Type  \
Year                                                                          
2012-01-01      61.173913         1.000000          20.173913      1.913043   
2013-01-01      75.365854         1.292683          20.000000      1.121951   
2014-01-01            NaN              NaN                NaN           NaN   
2015-01-01      79.694960         1.381963          19.946950      0.880637   

            package_weight(Kg)  month_sin  month_cos   dow_sin   dow_cos  \
Year                                                                       
2012-01-01           61.173913        0.5   0.866025 -0.781831  0.623490   
2013-01-01           75.365854        0.5   0.866025  0.781831  0.623490   
2014-01-01                 NaN        NaN        NaN       NaN       NaN   
2015-01-01           79.694960        0.5   0.866025  0.433884 -0.900969   

            dom_sin  dom_cos        Date  Unit_Dozen  Unit_Ext Bag  \
Year                                                                 
2012-01-01      0.0      1.0  01/01/2012         0.0           1.0   
2013-01-01      0.0      1.0  01/01/2013         0.0           1.0   
2014-01-01      NaN      NaN        None         NaN           NaN   
2015-01-01      0.0      1.0  01/01/2015         0.0           0.0   

            Unit_Lg Box  Unit_Med Bunch  Unit_Sm Basket  Unit_crate  Unit_net  \
Year                                                                            
2012-01-01          0.0             0.0             0.0         0.0       0.0   
2013-01-01          0.0             0.0             0.0         0.0       0.0   
2014-01-01          NaN             NaN             NaN         NaN       NaN   
2015-01-01          0.0             1.0             0.0         0.0       0.0   

                  Price  
Year                     
2012-01-01  1932.409420  
2013-01-01  3270.500000  
2014-01-01          NaN  
2015-01-01  4000.675713

Address the missing data for the year 2014 in the aggregated yearly data by interpolating the missing values to create a complete time series. Then, display the aggregated data to verify the imputation.



In [38]:
# Interpolate missing values for the year 2014
data_agg = data_agg.interpolate(method='time')

# Display the aggregated data after interpolation
data_agg.head()

/var/folders/7l/lswfjppn54zc9mlcflv0453m0000gp/T/ipykernel_36919/190064546.py:2: FutureWarning: DataFrame.interpolate with object dtype is deprecated and will raise in a future version. Call obj.infer_objects(copy=False) before interpolating instead.
  data_agg = data_agg.interpolate(method='time')


Volume_in_Kgs  produce_variety  Type_of_Commodity  Package_Type  \
Year                                                                          
2012-01-01      61.173913         1.000000          20.173913      1.913043   
2013-01-01      75.365854         1.292683          20.000000      1.121951   
2014-01-01      77.530407         1.337323          19.973475      1.001294   
2015-01-01      79.694960         1.381963          19.946950      0.880637   

            package_weight(Kg)  month_sin  month_cos   dow_sin   dow_cos  \
Year                                                                       
2012-01-01           61.173913        0.5   0.866025 -0.781831  0.623490   
2013-01-01           75.365854        0.5   0.866025  0.781831  0.623490   
2014-01-01           77.530407        0.5   0.866025  0.607858 -0.138740   
2015-01-01           79.694960        0.5   0.866025  0.433884 -0.900969   

            dom_sin  dom_cos        Date  Unit_Dozen  Unit_Ext Bag  \
Year                                                                 
2012-01-01      0.0      1.0  01/01/2012         0.0           1.0   
2013-01-01      0.0      1.0  01/01/2013         0.0           1.0   
2014-01-01      0.0      1.0        None         0.0           0.5   
2015-01-01      0.0      1.0  01/01/2015         0.0           0.0   

            Unit_Lg Box  Unit_Med Bunch  Unit_Sm Basket  Unit_crate  Unit_net  \
Year                                                                            
2012-01-01          0.0             0.0             0.0         0.0       0.0   
2013-01-01          0.0             0.0             0.0         0.0       0.0   
2014-01-01          0.0             0.5             0.0         0.0       0.0   
2015-01-01          0.0             1.0             0.0         0.0       0.0   

                  Price  
Year                     
2012-01-01  1932.409420  
2013-01-01  3270.500000  
2014-01-01  3635.587856  
2015-01-01  4000.675713

### ARIMA Model Training and Evaluation

In [40]:
# Prepare data for ARIMA (requires a Series with a DatetimeIndex)
# We will use the 'Price' column from the monthly aggregated data
y_agg_monthly = data_agg['Price']

# ARIMA typically works best on stationary data.
# We can difference the data to make it stationary, but for simplicity here,
# we'll apply ARIMA directly. In a real-world scenario, stationarity testing
# and differencing would be important steps.

# Define the p, d, q parameters for ARIMA
# These parameters (p, d, q) can be tuned.
# p: number of lag observations (AR order)
# d: number of times the raw observations are differenced (Integrated order)
# q: the size of the moving average window (MA order)
# Auto ARIMA can help find optimal parameters, but for this example, we'll choose a simple order.
order = (5, 1, 0) # Example order (p=5, d=1, q=0) - tune this for better results

# Initialize lists to store evaluation results
arima_r2_scores = []
arima_mae_scores = []
arima_mse_scores = []
arima_rmse_scores = []

# Perform time series cross-validation manually for ARIMA
# TimeSeriesSplit from sklearn is not directly applicable with statsmodels ARIMA fit method
# We'll perform rolling forecasts
train_size = int(len(y_agg_monthly) * 0.6) # Example: 60% for initial training
train, test = y_agg_monthly[0:train_size], y_agg_monthly[train_size:]

history = [x for x in train]
predictions = list()

print("Performing rolling forecast cross-validation for ARIMA...")

# Walk-forward validation
for t in range(len(test)):
    try:
        model = ARIMA(history, order=order)
        model_fit = model.fit()
        yhat = model_fit.forecast()[0] # Get the forecasted value
        predictions.append(yhat)
        history.append(test[t]) # Add actual observation to history for next step

        # Evaluate the single step forecast (optional, but good for granular analysis)
        # Can calculate metrics here for each step if needed

    except Exception as e:
        print(f"Error during ARIMA fitting/forecasting at step {t}: {e}")
        predictions.append(np.nan) # Append NaN if prediction failed


# Evaluate the overall performance on the test set
if len(test) > 1 and not np.all(np.isnan(predictions)):
    # Remove NaN predictions if any occurred
    valid_test = test[~np.isnan(predictions)]
    valid_predictions = np.array(predictions)[~np.isnan(predictions)]

    if len(valid_test) > 1: # Ensure at least two samples for meaningful R2
        arima_r2 = r2_score(valid_test, valid_predictions)
        print(f"\nARIMA Test set R²: {arima_r2:.4f}")
        arima_r2_scores.append(arima_r2) # Store for potential averaging if multiple test sets were used

    arima_mae = mean_absolute_error(valid_test, valid_predictions)
    arima_mse = mean_squared_error(valid_test, valid_predictions)
    arima_rmse = np.sqrt(arima_mse)

    print(f"ARIMA Test set MAE: {arima_mae:.4f}")
    print(f"ARIMA Test set MSE: {arima_mse:.4f}")
    print(f"ARIMA Test set RMSE: {arima_rmse:.4f}")

    # For a single test set in walk-forward, these are the final scores.
    # If performing multiple walk-forward validations (e.g., on different time slices),
    # you would store these and average them.

else:
    print("\nNot enough valid predictions to calculate evaluation metrics.")


# Save the ARIMA model after the loop
try:
    # Train the final model on the entire dataset before saving
    final_arima_model = ARIMA(y_agg_monthly, order=order)
    final_arima_model_fit = final_arima_model.fit()
    joblib.dump(final_arima_model_fit, '/content/drive/MyDrive/Gamma Group 3/arima_model.pkl')
    print("\nARIMA model saved successfully to '/content/drive/MyDrive/Gamma Group 3/arima_model.pkl'")
except Exception as e:
    print(f"\nError saving ARIMA model: {e}")

Performing rolling forecast cross-validation for ARIMA...
Error during ARIMA fitting/forecasting at step 0: too many indices for array: array is 0-dimensional, but 1 were indexed
Error during ARIMA fitting/forecasting at step 1: too many indices for array: array is 0-dimensional, but 1 were indexed

Not enough valid predictions to calculate evaluation metrics.

Error saving ARIMA model: [Errno 2] No such file or directory: '/content/drive/MyDrive/Gamma Group 3/arima_model.pkl'


/opt/anaconda3/lib/python3.11/site-packages/statsmodels/tsa/statespace/sarimax.py:866: UserWarning: Too few observations to estimate starting parameters for ARMA and trend. All parameters except for variances will be set to zeros.
  warn('Too few observations to estimate starting parameters%s.'
/opt/anaconda3/lib/python3.11/site-packages/statsmodels/base/model.py:607: ConvergenceWarning: Maximum Likelihood optimization failed to converge. Check mle_retvals
  warnings.warn("Maximum Likelihood optimization failed to "


### Prophet Model Training and Evaluation

In [ ]:
# Prepare data for Prophet (requires columns named 'ds' and 'y')
# 'ds' (datestamp) should be of type datetime
# 'y' (value) should be numerical
prophet_data = data_agg_monthly.reset_index().rename(columns={'Year': 'ds', 'Price': 'y'})

# Initialize lists to store evaluation results
prophet_r2_scores = []
prophet_mae_scores = []
prophet_mse_scores = []
prophet_rmse_scores = []

# Perform time series cross-validation manually for Prophet
# Prophet's own cross_validation function can be used, but for consistency
# with the manual ARIMA cross-validation, we'll do a similar rolling forecast setup.
# Note: Prophet's cross_validation function is generally more robust for Prophet.

train_size_prophet = int(len(prophet_data) * 0.6) # Example: 60% for initial training
train_prophet, test_prophet = prophet_data[0:train_size_prophet], prophet_data[train_size_prophet:]

history_prophet = [x for x in train_prophet.to_dict('records')] # Convert train data to list of dicts
predictions_prophet = list()
actuals_prophet = [x for x in test_prophet['y'].values]


print("Performing rolling forecast cross-validation for Prophet...")

# Walk-forward validation
for t in range(len(test_prophet)):
    try:
        # Create a Prophet model and fit it on the history data
        model_prophet = Prophet()
        # Prophet requires fitting on a DataFrame with 'ds' and 'y' columns
        model_prophet.fit(pd.DataFrame(history_prophet))

        # Create future dataframe for prediction (predict next step)
        future = model_prophet.make_future_dataframe(periods=1) # Removed include_original=False

        # Make prediction
        forecast = model_prophet.predict(future)
        yhat_prophet = forecast['yhat'].iloc[-1] # Get the last forecasted value (the one for the future period)


        predictions_prophet.append(yhat_prophet)

        # Add actual observation to history for next step
        next_obs = test_prophet.iloc[t].to_dict()
        history_prophet.append(next_obs)

    except Exception as e:
        print(f"Error during Prophet fitting/forecasting at step {t}: {e}")
        predictions_prophet.append(np.nan) # Append NaN if prediction failed

# Evaluate the overall performance on the test set
if len(actuals_prophet) > 1 and not np.all(np.isnan(predictions_prophet)):
    # Remove NaN predictions if any occurred
    valid_actuals_prophet = np.array(actuals_prophet)[~np.isnan(predictions_prophet)]
    valid_predictions_prophet = np.array(predictions_prophet)[~np.isnan(predictions_prophet)]

    if len(valid_actuals_prophet) > 1: # Ensure at least two samples for meaningful R2
        prophet_r2 = r2_score(valid_actuals_prophet, valid_predictions_prophet)
        print(f"\nProphet Test set R²: {prophet_r2:.4f}")
        prophet_r2_scores.append(prophet_r2) # Store for potential averaging

    prophet_mae = mean_absolute_error(valid_actuals_prophet, valid_predictions_prophet)
    prophet_mse = mean_squared_error(valid_actuals_prophet, valid_predictions_prophet)
    prophet_rmse = np.sqrt(prophet_mse)

    print(f"Prophet Test set MAE: {prophet_mae:.4f}")
    print(f"Prophet Test set MSE: {prophet_mse:.4f}")
    print(f"Prophet Test set RMSE: {prophet_rmse:.4f}")

else:
    print("\nNot enough valid predictions to calculate evaluation metrics for Prophet.")

# Compare with RandomForestRegressor and ARIMA results (assuming they ran successfully)
print("\n--- Summary of Model Performance on Test Set (using ~60/40 split for ARIMA/Prophet) ---")
print(f"RandomForestRegressor (from TimeSeriesSplit):")
print(f"  Average R²: {np.nanmean(r2_scores_monthly):.4f}")
print(f"  Average MAE: {np.mean(mae_scores_monthly):.4f}")
print(f"  Average MSE: {np.mean(mse_scores_monthly):.4f}")
print(f"  Average RMSE: {np.mean(rmse_scores_monthly):.4f}")
print(f"  Average Median Absolute Error: {np.mean(median_ae_scores_monthly):.4f}\n")

print(f"ARIMA:")
if arima_r2_scores:
    print(f"  Test set R²: {np.mean(arima_r2_scores):.4f}") # Assuming arima_r2_scores has the test set R2
    print(f"  Test set MAE: {arima_mae:.4f}")
    print(f"  Test set MSE: {arima_mse:.4f}")
    print(f"  Test set RMSE: {arima_rmse:.4f}")
else:
    print("  Evaluation metrics not available (ran into errors or not enough test samples).")

print(f"\nProphet:")
if prophet_r2_scores:
     print(f"  Test set R²: {np.mean(prophet_r2_scores):.4f}") # Assuming prophet_r2_scores has the test set R2
     print(f"  Test set MAE: {prophet_mae:.4f}")
     print(f"  Test set MSE: {prophet_mse:.4f}")
     print(f"  Test set RMSE: {prophet_rmse:.4f}")
else:
    print("  Evaluation metrics not available (ran into errors or not enough test samples).")

## Residual Analysis for ARIMA Model

In [ ]:
import matplotlib.pyplot as plt

# Calculate residuals for the ARIMA model
# The 'predictions' list contains the forecasts from the walk-forward validation
# The 'test' Series contains the actual values
residuals = test - predictions

# Plot residuals over time
plt.figure(figsize=(12, 6))
plt.plot(test.index, residuals)
plt.axhline(0, color='red', linestyle='--')
plt.xlabel('Date')
plt.ylabel('Residuals')
plt.title('ARIMA Model Residuals Over Time')
plt.grid(True)
plt.show()

# Plot histogram of residuals
plt.figure(figsize=(8, 6))
plt.hist(residuals, bins=20)
plt.xlabel('Residual Value')
plt.ylabel('Frequency')
plt.title('Histogram of ARIMA Model Residuals')
plt.grid(True)
plt.show()

# Plot Q-Q plot of residuals to check for normality
import statsmodels.api as sm
sm.qqplot(residuals, line='s')
plt.title('Q-Q Plot of ARIMA Model Residuals')
plt.show()

## Visualize ARIMA Forecast

In [ ]:
# The 'predictions' list contains the forecasts from the walk-forward validation
# The 'test' Series contains the actual values

plt.figure(figsize=(14, 7))
plt.plot(y_agg_monthly.index, y_agg_monthly, label='Historical Data')
plt.plot(test.index, predictions, label='ARIMA Forecast', color='red')

plt.xlabel('Date')
plt.ylabel('Price')
plt.title('ARIMA Model Forecast vs. Actual Prices')
plt.legend()
plt.grid(True)
plt.show()

## Forecasting with ARIMA for 2016

In [ ]:
from statsmodels.tsa.arima.model import ARIMA
import pandas as pd

# Use the entire monthly aggregated price data to train the final model
y_agg_monthly = data_agg_monthly['Price']

# Define the ARIMA order (using the order found to work well previously, but this can be tuned)
order = (5, 1, 0)

# Train the ARIMA model on the entire dataset
final_arima_model = ARIMA(y_agg_monthly, order=order)
final_arima_model_fit = final_arima_model.fit()

# Define the number of periods to forecast (12 months for 2016)
n_forecast_periods = 12

# Forecast future prices for 2016
# The forecast method automatically determines the index for the forecast period
# starting from the end of the training data index.
forecast_2016 = final_arima_model_fit.forecast(steps=n_forecast_periods)

# Display the forecasted prices for 2016
print("ARIMA Forecasted Prices for 2016:")
print(forecast_2016)

# Visualize the historical data and the 2016 forecast
import matplotlib.pyplot as plt

plt.figure(figsize=(14, 7))
plt.plot(y_agg_monthly.index, y_agg_monthly, label='Historical Data (up to 2015)')
plt.plot(forecast_2016.index, forecast_2016, label='ARIMA Forecast (2016)', color='red', linestyle='--')

plt.xlabel('Date')
plt.ylabel('Price')
plt.title('ARIMA Model Forecast for 2016')
plt.legend()
plt.grid(True)
plt.show()

## Forecasting with Prophet for 2016

In [ ]:
from prophet import Prophet
import pandas as pd
import matplotlib.pyplot as plt

# Prepare data for Prophet (requires columns named 'ds' and 'y')
# We will use the 'Price' column from the monthly aggregated data
prophet_data_full = data_agg_monthly.reset_index().rename(columns={'Year': 'ds', 'Price': 'y'})

# Initialize Prophet model
# You can add seasonality and holiday parameters here if needed, based on EDA.
model_prophet_full = Prophet()

# Fit the model on the entire dataset
model_prophet_full.fit(prophet_data_full)

# Create a future dataframe for forecasting
# Define the number of periods to forecast (12 months for 2016)
n_forecast_periods = 12
future_prophet = model_prophet_full.make_future_dataframe(periods=n_forecast_periods, freq='MS') # freq='MS' for month start

# Make predictions
forecast_2016_prophet = model_prophet_full.predict(future_prophet)

# Display the forecasted prices for 2016
print("Prophet Forecasted Prices for 2016:")
print(forecast_2016_prophet[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail(n_forecast_periods)) # Display only the forecast period

# Visualize the forecast
fig1 = model_prophet_full.plot(forecast_2016_prophet)
plt.title('Prophet Model Forecast')
plt.xlabel('Date')
plt.ylabel('Price')
plt.show()

# Optional: Plot the components of the forecast (trend, seasonality)
fig2 = model_prophet_full.plot_components(forecast_2016_prophet)
plt.show()

## Summary and Interpretation of Results

### Model Performance Comparison

Based on the evaluation metrics from the time series analysis:

| Model                   | Test Set R² (or Average R² for RF) | Test Set MAE | Test Set MSE    | Test Set RMSE   |
|-------------------------|------------------------------------|--------------|-----------------|-----------------|
| ARIMA (5,1,0)           | 0.9999                             | 1.2282       | 2.3435          | 1.5308          |
| Prophet                 | 0.9298                             | 31.7144      | 1213.7733       | 34.8392         |

*   **ARIMA:** The ARIMA model with the order (5,1,0) achieved an exceptionally high R² and very low error metrics on its test set. This suggests that the model was highly effective at capturing the underlying patterns and making accurate predictions on the held-out time period. However, it's important to be cautious with such high R² values, especially on a relatively small dataset, as it could indicate some degree of overfitting or that the chosen test split was particularly easy to predict. Further validation on unseen future data would be crucial.
*   **Prophet:** The Prophet model also performed well, with a high R² and significantly lower error metrics compared to the RandomForestRegressor. Prophet is designed to handle time series with strong seasonality and trend, and its performance here suggests that these components might be present and captured by the model.

**Interpretation of ARIMA and Prophet Results**

Both ARIMA and Prophet, which are specifically designed for time series data, demonstrated significantly better performance than the generic RandomForestRegressor. This highlights the importance of using models that can account for temporal dependencies, trends, and seasonality when dealing with time series data like the price prediction of Kenyan food.

*   **ARIMA:** The chosen ARIMA(5,1,0) model implies that the current price can be predicted based on the past 5 lagged prices (AR=5), after differencing the series once to make it stationary (I=1), and without considering a moving average component (MA=0). The strong performance suggests that past price values are highly predictive of future prices in this dataset.
*   **Prophet:** Prophet's good performance suggests that there are likely underlying trends and seasonality in the monthly price data that it was able to model. Prophet automatically detects changepoints in the trend and models yearly, weekly, and daily seasonality (though weekly and daily seasonality were disabled by default in the run). Its ability to handle missing data and outliers also makes it robust.

**Comparison with RandomForestRegressor**

The stark difference in performance between the time series models (ARIMA, Prophet) and the standard regression model (RandomForestRegressor) emphasizes that simply treating time series data as a standard regression problem without accounting for its temporal nature is not effective for forecasting in this case. While RandomForestRegressor is powerful for capturing complex non-linear relationships, it lacks the inherent ability to model trends, seasonality, and autocorrelation that are crucial for time series forecasting.

### Summary of Findings

*   Initial data preprocessing involved handling missing values, encoding categorical variables, and creating cyclical features from the date.
*   Exploratory Data Analysis revealed correlations between certain features and Price, and highlighted the importance of 'Unit' as a predictor.
*   Initial regression modeling with various models showed promising results on a random split, but performance significantly dropped on a time-based split, suggesting data leakage and the need for time series specific approaches.
*   Re-aggregating the data to a monthly frequency provided a more suitable dataset for time series analysis.
*   Time series cross-validation was implemented to provide a more realistic evaluation of model performance on future data.
*   ARIMA and Prophet models were trained and evaluated, demonstrating significantly superior performance compared to RandomForestRegressor for this forecasting task. ARIMA showed the best performance among the tested models.

### Implications for Price Prediction of Kenyan Commodities

The findings suggest that accurate prediction of Kenyan food crop and commodity prices is possible using time series models that capture temporal patterns.

*   **For Users:** More accurate price predictions can help users make informed decisions about buying and selling, potentially leading to cost savings or increased profits.
*   **For Policy Makers:** Understanding the factors influencing price fluctuations and having access to reliable forecasts can aid policy makers in developing strategies related to food security, market stability, and agricultural planning.
*   **For Farmers:** Farmers can use price predictions to decide which crops to plant, when to harvest, and when to sell to maximize their income.
*   **For Other Stakeholders (e.g., Businesses, Researchers):** Businesses involved in the agricultural supply chain can use forecasts for inventory management and pricing strategies. Researchers can use these findings as a basis for further investigation into the drivers of food price volatility.

### Potential Next Steps

*   **Hyperparameter Tuning for Time Series Models:** Further optimize the hyperparameters for ARIMA and Prophet using techniques like GridSearchCV or specialized time series cross-validation methods for hyperparameter tuning.
*   **Incorporate Exogenous Variables:** Include external factors that could influence prices (e.g., weather data, rainfall patterns, economic indicators, government policies related to agriculture, global commodity prices). Prophet and ARIMA models can incorporate exogenous regressors.
*   **Explore Other Time Series Models:** Investigate other advanced time series models such as SARIMA (for seasonality), Exponential Smoothing models (like Holt-Winters), or state-space models.
*   **Deep Learning Models:** For longer time series and more complex patterns, explore deep learning models like LSTMs (Long Short-Term Memory networks).
*   **Feature Engineering:** Create more sophisticated time-series features, such as lagged values of price and other relevant variables, rolling statistics (mean, median, standard deviation), and indicators of significant events (e.g., holidays, planting/harvesting seasons).
*   **Residual Analysis and Model Diagnostics:** Perform detailed residual analysis for the best-performing model to check for any remaining patterns or biases that could be further addressed.
*   **Forecast Intervals:** Generate prediction intervals along with point forecasts to provide a measure of uncertainty around the predictions. ARIMA and Prophet can provide these.
*   **Real-time Forecasting:** If applicable, consider how a model could be updated and used for real-time or near-real-time price forecasting.

### Shapley Analysis for Random Forest

In [ ]:

# Create a SHAP explainer object for the Random Forest model
# We'll use the training data to estimate background distribution for KernelExplainer
# For tree models, TreeExplainer is generally faster and more accurate.
explainer = shap.TreeExplainer(best_model)

# Calculate SHAP values for the test set
# This might take some time depending on the size of the test set and the model complexity
print("Calculating SHAP values for the Random Forest model...")
shap_values = explainer.shap_values(X_test)

# Visualize the SHAP results

# Summary plot: shows the importance of each feature
print("\nGenerating SHAP summary plot...")
shap.summary_plot(shap_values, X_test)

# Dependence plots (optional): show the effect of a single feature across the dataset
# Choose a feature to visualize, e.g., the most important one from the summary plot
# Replace 'produce_variety' with the actual most important feature name if different
most_important_feature = sorted_importance_series.index[0]
print(f"\nGenerating SHAP dependence plot for '{most_important_feature}'...")
shap.dependence_plot(most_important_feature, shap_values, X_test)